In [1]:
#!/usr/bin/python

import sys
sys.path.append("../src")
import gym
import tensorflow as tf
import numpy as np
from tqdm import tqdm
import wandb
from config import *
from replay_buffer import *
from networks import *
from agent import *
from tcl_env_dqn_1 import *

config = dict(
  learning_rate_actor = ACTOR_LR,
  learning_rate_critic = ACTOR_LR,
  batch_size = BATCH_SIZE,
  architecture = "DDPG",
  env = MicroGridEnv
)

wandb.init(
  project=f"tensorflow2_ddpg_{ENV_NAME.lower()}",
  tags=["DDPG", "FCL", "RL"],
  config=config,
)

env = MicroGridEnv()
agent = Agent(env)

scores = []
evaluation = True


NUM_STATE = env.observation_space.shape[0]
NUM_ACTIONS = env.action_space.n
NUM_ACTIONS_TCLs = 4
NUM_ACTIONS_PRICES = 5
NUM_ACTIONS_DEF = 2
NUM_ACTIONS_EXCESS = 2


if PATH_LOAD is not None:
    print("loading weights")
    observation = env.reset()
    action = agent.actor(observation[None, :])
    agent.target_actor(observation[None, :])
    agent.critic(observation[None, :], action)
    agent.target_critic(observation[None, :], action)
    agent.load()
    print(agent.replay_buffer.buffer_counter)
    print(agent.replay_buffer.n_games)
    print(agent.noise)

for _ in tqdm(range(MAX_GAMES)):
    start_time = time.time()
    states = env.reset()
    done = False
    score = 0
    while not done:
        action = agent.get_action(states)
        new_states, reward, done, info = env.step(action)
        score += reward
        agent.add_to_replay_buffer(states, action, reward, new_states, done)
        agent.learn()
        states = new_states
        
    agent.replay_buffer.update_n_games()
    
    scores.append(score)
    

    wandb.log({'Game number': agent.replay_buffer.n_games, '# Episodes': agent.replay_buffer.buffer_counter, 
               "Average reward": round(np.mean(scores[-10:]), 2), \
                      "Time taken": round(time.time() - start_time, 2)})

    if (_ + 1) % EVALUATION_FREQUENCY == 0:
        evaluation = True
        states = env.reset()
        done = False
        score = 0
        while not done:
            action = agent.get_action(states)
            new_states, reward, done, info = env.step(action)
            score += reward
            states = new_states
        wandb.log({'Game number': agent.replay_buffer.n_games, 
                   '# Episodes': agent.replay_buffer.buffer_counter, 
                   'Evaluation score': score})
        evaluation = False
     
    if (_ + 1) % SAVE_FREQUENCY == 0:
        print("saving...")
        agent.save()
        print("saved")


C:\Users\47939\anaconda3\lib\site-packages\jupyter_server\services\config\manager.py:17: DeprecationWarning: metadata {'default': 'serverconfig'} was set from the constructor. With traitlets 4.1, metadata should be set using the .tag() method, e.g., Int().tag(key1='value1', key2='value2')
  config_dir_name = Unicode(
Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: mehdifo (use `wandb login --relogin` to force relogin)


  0%|          | 1/250 [00:00<00:36,  6.79it/s]

Day: 0
[39.316105 48.91329  39.24497  30.2038   42.044685 39.035942 45.638866
 39.461044 44.615364 41.26308  47.523518 43.97259  33.565163 32.990955
 46.55847  36.84095  39.297035 48.23243  41.183018 35.63421  37.731632
 37.722614 38.35421  42.385742 47.11592  37.001377 43.355217 35.20985
 35.7304   32.4935   42.372475 37.62294  43.630165 45.44644  42.028812
 39.010822 42.38453  51.25507  43.658375 44.25004  41.205635 32.885612
 43.20745  36.58088  37.108253 32.714577 42.805275 40.89406  32.74644
 45.4273   35.92122  42.296467 42.63742  47.73052  38.911255 42.762794
 36.549374 44.404102 39.873634 36.497208 40.39696  36.928005 42.79161
 39.79251  32.490425 31.501625 44.305477 40.89478  43.977882 42.79697
 45.21698  41.911465 38.098255 45.29628  39.433308 41.36483  47.81021
 31.93468  39.82369  47.727356]
40
[39.29853  50.111732 40.603886 27.47385  44.557995 38.844574 45.021915
 39.138718 43.07624  39.480946 49.936413 44.27716  30.97872  31.540396
 46.14626  38.543568 41.063026 49.634396

[37.75475  54.91695  39.4978   24.254799 46.74509  41.906715 48.04375
 39.25174  45.354214 34.07347  46.467163 48.367577 23.886843 26.719383
 40.43239  38.308895 41.277576 55.476273 35.45525  34.086338 34.28656
 41.715946 38.672455 42.590454 47.117504 30.757286 40.129093 37.791553
 26.774887 32.139572 46.01349  41.084896 44.40372  51.04504  46.773014
 39.205555 41.435772 52.883144 45.59828  43.028267 35.806816 30.980242
 46.12503  38.091503 38.937454 28.501034 46.964424 38.13459  27.55085
 45.638348 29.910446 41.195457 49.633175 48.56296  36.644947 45.163376
 28.134928 45.432392 39.50358  39.496197 37.388542 34.009274 39.43499
 37.242706 32.584785 25.160141 48.695374 45.680218 46.83752  47.87075
 53.354446 33.977463 35.76102  46.980972 37.74269  45.72395  53.478783
 28.052525 36.882362 51.264214]
40
[37.524544 55.390186 39.477955 23.320086 46.352825 41.834137 48.459427
 38.64911  45.582294 33.66749  45.82392  48.744053 23.972063 27.014088
 40.222824 38.17927  41.359505 55.637444 35.616

  1%|          | 2/250 [00:00<00:51,  4.79it/s]

...

[7.9999001e+01 8.0000000e+01 7.9999992e+01 8.0000000e+01 5.0299703e-03
 7.9999954e+01 8.0000000e+01 3.6384273e+00 1.2443260e-03 7.9999733e+01
 8.0000000e+01 8.0000000e+01 1.4258379e-03 3.0361677e-03 7.9999054e+01
 1.2817383e-02 7.9999985e+01 8.0000000e+01 7.2929170e-03 7.9999794e+01
 8.0000000e+01 9.8027857e-03 9.9039078e-03 7.9991043e+01 7.9996468e+01
 7.9999893e+01 4.6822326e-03 7.9999199e+01 5.1682896e-04 2.5283077e-04
 7.9999847e+01 8.0000000e+01 8.0000000e+01 8.0000000e+01 8.0000000e+01
 7.9999985e+01 3.4506710e-03 8.0000000e+01 8.1024214e-04 3.2520294e-02
 7.9998512e+01 7.9999954e+01 6.3309202e-04 2.3748376e-04 8.0000000e+01
 4.4695260e-03 8.0000000e+01 7.9999969e+01 1.4394587e-04 1.7690659e-02
 8.3237137e-05 2.4826527e-02 8.0000000e+01 8.0000000e+01 3.6638230e-03
 1.0625344e-03 7.9999969e+01 7.9999985e+01 6.3374350e-03 7.9999962e+01
 7.9999863e+01 1.0142326e-02 7.9999939e+01 1.8043518e-02 2.1919233e-04
 1.2470001e-03 8.0000000e+01 8.0000000e+01 8.8350778e-04 7.9999908e+01
 8.000

[7.9999619e+01 8.0000000e+01 8.0000000e+01 8.0000000e+01 2.3555467e-03
 7.9999985e+01 8.0000000e+01 1.5476704e-01 5.8698026e-04 7.9999878e+01
 8.0000000e+01 8.0000000e+01 6.5178901e-04 1.3853409e-03 7.9999687e+01
 7.0591127e-03 8.0000000e+01 8.0000000e+01 3.2576090e-03 7.9999893e+01
 8.0000000e+01 5.3762388e-03 4.7398969e-03 7.9996330e+01 7.9998558e+01
 7.9999969e+01 2.5156531e-03 7.9999695e+01 1.9078645e-04 1.0632859e-04
 7.9999954e+01 8.0000000e+01 8.0000000e+01 8.0000000e+01 8.0000000e+01
 8.0000000e+01 1.7959643e-03 8.0000000e+01 3.8928934e-04 1.6534328e-02
 7.9999481e+01 8.0000000e+01 2.5578763e-04 9.1912727e-05 8.0000000e+01
 2.3174312e-03 8.0000000e+01 8.0000000e+01 5.3431122e-05 8.7865405e-03
 3.1047934e-05 1.3334751e-02 8.0000000e+01 8.0000000e+01 1.6698022e-03
 4.9057789e-04 8.0000000e+01 8.0000000e+01 3.1710253e-03 7.9999992e+01
 7.9999954e+01 5.4726382e-03 7.9999985e+01 1.0626316e-02 9.2027360e-05
 5.7246222e-04 8.0000000e+01 8.0000000e+01 4.0108516e-04 7.9999969e+01
 8.000

100%|██████████| 250/250 [05:46<00:00,  1.58s/it]

[7.9999619e+01 8.0000000e+01 8.0000000e+01 8.0000000e+01 2.3892208e-03
 7.9999992e+01 8.0000000e+01 5.2418709e-02 6.2009483e-04 7.9999863e+01
 8.0000000e+01 8.0000000e+01 6.9006509e-04 1.4259928e-03 7.9999710e+01
 7.3939720e-03 8.0000000e+01 8.0000000e+01 3.2122131e-03 7.9999878e+01
 8.0000000e+01 5.7546981e-03 4.7933091e-03 7.9996574e+01 7.9998634e+01
 7.9999969e+01 2.6384217e-03 7.9999702e+01 1.8690298e-04 1.1515934e-04
 7.9999962e+01 8.0000000e+01 8.0000000e+01 8.0000000e+01 8.0000000e+01
 8.0000000e+01 1.9408970e-03 8.0000000e+01 4.2685727e-04 1.6119480e-02
 7.9999527e+01 8.0000000e+01 2.5936638e-04 9.5096431e-05 8.0000000e+01
 2.4631028e-03 8.0000000e+01 8.0000000e+01 5.5141612e-05 8.8229319e-03
 3.2202090e-05 1.3430119e-02 8.0000000e+01 8.0000000e+01 1.7094542e-03
 5.1276537e-04 8.0000000e+01 8.0000000e+01 3.2538301e-03 7.9999985e+01
 7.9999954e+01 5.6902366e-03 7.9999985e+01 1.1584759e-02 9.7977470e-05
 5.9341080e-04 8.0000000e+01 8.0000000e+01 4.2078245e-04 7.9999985e+01
 8.000

100%|██████████| 250/250 [05:46<00:00,  1.39s/it]
